In [ ]:
%%capture
import os, re
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth
else:
    # Do this only in Colab notebooks! Otherwise use pip install unsloth
    import torch; v = re.match(r"[0-9]{1,}\.[0-9]{1,}", str(torch.__version__)).group(0)
    xformers = "xformers==" + ("0.0.33.post1" if v=="2.9" else "0.0.32.post2" if v=="2.8" else "0.0.29.post3")
    !pip install --no-deps bitsandbytes accelerate {xformers} peft trl triton cut_cross_entropy unsloth_zoo
    !pip install sentencepiece protobuf "datasets==4.3.0" "huggingface_hub>=0.34.0" hf_transfer
    !pip install --no-deps unsloth
# Install transformers branch for Ministral
!pip install git+https://github.com/huggingface/transformers.git@bf3f0ae70d0e902efab4b8517fce88f6697636ce
!pip install --no-deps trl==0.22.2

In [ ]:
ministral_models = [
    "unsloth/Ministral-3-3B-Instruct-2512", # Ministral instruct models
    "unsloth/Ministral-3-8B-Instruct-2512",
    "unsloth/Ministral-3-14B-Instruct-2512",

    "unsloth/Ministral-3-3B-Reasoning-2512", # Ministral reasoning models
    "unsloth/Ministral-3-8B-Reasoning-2512",
    "unsloth/Ministral-3-14B-Reasoning-2512",

    "unsloth/Ministral-3-3B-Base-2512", # Ministral base models
    "unsloth/Ministral-3-8B-Base-2512",
    "unsloth/Ministral-3-14B-Base-2512",
]

In [ ]:
#Hyperparamters
max_seq_length = 2048
dtype = None # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
load_in_4bit = True # Use 4bit to reduce memory use. False for 16bit LoRA.
#load_in_8bit = False # Use 8bit quantization to reduce memory usage. Can be False.
epoch = 1
MODEL_ID = "unsloth/Ministral-3-3B-Instruct-2512"
MODEL = "Ministral-3-3B-Instruct-2512"
chat_template = "mistral"

#Huggingface settings
HF_USERNAME = "schmuelling"
MODEL_NAME = f"{MODEL}-finetome"

## Set up HuggingFace

In [ ]:

from huggingface_hub import login
import os

HF_TOKEN = input("Access Token: ").strip()
login(token=HF_TOKEN)

os.environ["HF_TOKEN"] = HF_TOKEN

In [ ]:
# Checkpoint repo (for training)
checkpoint_repo_id = f"{HF_USERNAME}/{MODEL_NAME}-checkpoint"

#repo (for final quantized models)
repo_id = f"{HF_USERNAME}/{MODEL_NAME}"

## Load model

In [ ]:
from unsloth import FastVisionModel
import torch
from huggingface_hub import repo_exists
from unsloth.chat_templates import get_chat_template

# Check if checkpoint repo exists and load accordingly
if repo_exists(checkpoint_repo_id, token=HF_TOKEN):
    print(f"Loading from checkpoint: {checkpoint_repo_id}")
    model, tokenizer = FastVisionModel.from_pretrained(
        checkpoint_repo_id,
        load_in_4bit=load_in_4bit,
        use_gradient_checkpointing = "unsloth",
        token = HF_TOKEN,
    )
    resume_training = True
else:
    print(f"Loading base model: {MODEL_ID}")
    model, tokenizer = FastVisionModel.from_pretrained(
        MODEL_ID,
        load_in_4bit=load_in_4bit,
        use_gradient_checkpointing = "unsloth",
    )
    resume_training = False


tokenizer = get_chat_template(
    tokenizer,
    chat_template = chat_template,
)


🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
🦥 Unsloth Zoo will now patch everything to make training faster!
Loading base model: unsloth/Ministral-3-3B-Instruct-2512


Unrecognized keys in `rope_parameters` for 'rope_type'='yarn': {'max_position_embeddings'}


==((====))==  Unsloth 2025.11.6: Fast Ministral3 patching. Transformers: 5.0.0.dev0.
   \\   /|    NVIDIA A100-SXM4-80GB. Num GPUs = 1. Max memory: 79.318 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.9.0+cu126. CUDA: 8.0. CUDA Toolkit: 12.6. Triton: 3.5.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.33.post1. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!


Unrecognized keys in `rope_parameters` for 'rope_type'='yarn': {'max_position_embeddings'}
Unrecognized keys in `rope_parameters` for 'rope_type'='yarn': {'max_position_embeddings'}


model.safetensors.index.json: 0.00B [00:00, ?B/s]

...

processor_config.json:   0%|          | 0.00/976 [00:00<?, ?B/s]

chat_template.jinja: 0.00B [00:00, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

Add LoRA adapters.

In [ ]:
if not resume_training:

    model = FastVisionModel.get_peft_model(
        model,
        finetune_vision_layers     = False, # False if not finetuning vision layers
        finetune_language_layers   = True, # False if not finetuning language layers
        finetune_attention_modules = True, # False if not finetuning attention layers
        finetune_mlp_modules       = True, # False if not finetuning MLP layers

        r = 16,           # The larger, the higher the accuracy, but might overfit
        lora_alpha = 16,  # Recommended alpha == r at least
        lora_dropout = 0,
        bias = "none",
        random_state = 3407,
        use_rslora = False,  # We support rank stabilized LoRA
        loftq_config = None, # And LoftQ
        # target_modules = "all-linear", # Optional now! Can specify a list if needed
    )

Unsloth: Making `model.base_model.model.model.language_model` require gradients


## Data Prep

In [ ]:
from unsloth.chat_templates import get_chat_template

# This cell now only defines the formatting function and loads the dataset.
# The tokenizer setup will happen after the model is loaded.

def formatting_prompts_func(examples):
    convos = examples["conversations"]
    texts = [tokenizer.apply_chat_template(convo, tokenize = False, add_generation_prompt = False) for convo in convos]
    return { "text" : texts, }
pass

from datasets import load_dataset
dataset = load_dataset("mlabonne/FineTome-100k", split = "train")

README.md:   0%|          | 0.00/982 [00:00<?, ?B/s]

data/train-00000-of-00001.parquet:   0%|          | 0.00/117M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/100000 [00:00<?, ? examples/s]

### Format from ShareGPT to HuggingFace's generic format to bring it eventually into the correspoinding chat format of the model.


```
{"from": "system", "value": "You are an assistant"}
{"from": "human", "value": "What is 2+2?"}
{"from": "gpt", "value": "It's 4."}
```
to
```
{"role": "system", "content": "You are an assistant"}
{"role": "user", "content": "What is 2+2?"}
{"role": "assistant", "content": "It's 4."}
```

In [ ]:
from unsloth.chat_templates import standardize_sharegpt
dataset = standardize_sharegpt(dataset)
dataset = dataset.map(formatting_prompts_func, batched = True,)

Unsloth: Standardizing formats (num_proc=12):   0%|          | 0/100000 [00:00<?, ? examples/s]

Map:   0%|          | 0/100000 [00:00<?, ? examples/s]

## Set the trainer up

In [ ]:
from trl import SFTTrainer, SFTConfig
from transformers import DataCollatorForSeq2Seq
import torch, os, gc
from unsloth import FastLanguageModel, is_bfloat16_supported


In [ ]:
from trl import SFTConfig
from unsloth import is_bfloat16_supported

trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset,
    dataset_text_field = "text",
    max_seq_length = max_seq_length,
    data_collator = DataCollatorForSeq2Seq(tokenizer = tokenizer),
    dataset_num_proc = 2,
    packing = False,
    args = SFTConfig(
        per_device_train_batch_size = 2,
        gradient_accumulation_steps = 4,
        warmup_steps = 20,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 5,
        save_steps = 1000,
        save_total_limit = 3,
        optim = "adamw_8bit",
        weight_decay = 0.001,
        lr_scheduler_type = "linear",
        #max_steps = 100,
        num_train_epochs = 1,
        seed = 3407,
        output_dir = "outputs",
        report_to = "tensorboard",

        # HuggingFace Hub integration
        push_to_hub = True,
        hub_model_id = checkpoint_repo_id,
        hub_strategy = "checkpoint",  # push on every save
    ),
)

warmup_ratio is deprecated and will be removed in v5.2. Use `warmup_steps` instead.


Unsloth: Tokenizing ["text"] (num_proc=16):   0%|          | 0/100000 [00:00<?, ? examples/s]

## Finetuning

In [ ]:
#first things first check for available GPUs

device_name = torch.cuda.get_device_name(0)
print("GPU:", device_name)
print("CUDA available:", torch.cuda.is_available())


GPU: NVIDIA A100-SXM4-80GB
CUDA available: True


In [ ]:
%load_ext tensorboard
%tensorboard --logdir outputs/logs

<IPython.core.display.Javascript object>

In [ ]:
if resume_training:
    print("Will resume training.")
    trainer_stats = trainer.train(resume_from_checkpoint=True)
else:
    print("Will start training from scratch.")
    trainer_stats = trainer.train()


The model is already on multiple devices. Skipping the move to device specified in `args`.


Will start training from scratch.


==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 100,000 | Num Epochs = 1 | Total steps = 12,500
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 4 x 1) = 8
 "-____-"     Trainable parameters = 24,707,072 of 3,873,797,120 (0.64% trained)
Unrecognized keys in `rope_parameters` for 'rope_type'='yarn': {'max_position_embeddings'}


Unsloth: Will smartly offload gradients to save VRAM!


In [ ]:
# @title Show final memory and time stats
import torch

# Define max_memory:
if torch.cuda.is_available():
    max_memory = torch.cuda.get_device_properties(0).total_memory / 1024 / 1024 / 1024
else:
    # Set a default max_memory if no CUDA device is available to prevent errors
    max_memory = 16.0 # Example: 16 GB, adjust as needed for your environment


start_gpu_memory = 0.0


used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory / max_memory * 100, 3)
lora_percentage = round(used_memory_for_lora / max_memory * 100, 3)

# trainer_stats should be available from previous cell execution.
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(
    f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training."
)
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

25751.7924 seconds used for training.
429.2 minutes used for training.
Peak reserved memory = 6.896 GB.
Peak reserved memory for training = 6.896 GB.
Peak reserved memory % of max memory = 8.694 %.
Peak reserved memory for training % of max memory = 8.694 %.


## Save Model

In [ ]:
#model.save_pretrained_gguf(repo_id, tokenizer, quantization_method = "q4_k_m")

In [ ]:
# save to hub
#model.push_to_hub_gguf(
#    repo_id,
#    tokenizer,
#    quantization_method = ["q4_k_m"],
#    token = HF_TOKEN,
#)

In [ ]:
# saving for vLLM or Transformer
model.save_pretrained_merged(repo_id, tokenizer, save_method = "merged_4bit_forced")
#model.push_to_hub_merged(repo_id, tokenizer, save_method = "merged_4bit_forced", token = HF_TOKEN)

Unsloth: Merging LoRA weights into 4bit model...


/usr/local/lib/python3.12/dist-packages/peft/tuners/lora/bnb.py:397: UserWarning: Merge lora module to 4-bit linear may get different generations due to rounding errors.
  warnings.warn(
Unrecognized keys in `rope_parameters` for 'rope_type'='yarn': {'max_position_embeddings'}


Unsloth: Merging finished.
Unsloth: Found skipped modules: ['model.multi_modal_projector.patch_merger.merging_layer', 'model.multi_modal_projector.linear_1', 'model.multi_modal_projector.linear_2', 'lm_head']. Updating config.
Unsloth: Saving merged 4bit model to schmuelling/Ministral-3-3B-Instruct-2512-finetome...
Unsloth: Merged 4bit model saved.
Unsloth: Merged 4bit model process completed.


In [ ]:
#model.push_to_hub_merged(repo_id, tokenizer, save_method = "merged_4bit_forced", token = HF_TOKEN)

In [ ]:
from huggingface_hub import HfApi, create_repo

create_repo(repo_id=repo_id, token=HF_TOKEN, exist_ok=True)

api = HfApi()
api.upload_folder(
    folder_path=repo_id,
    repo_id=repo_id,
    token=HF_TOKEN,
)

Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...2-finetome/tokenizer.json: 100%|##########| 17.1MB / 17.1MB            

  ...inetome/model.safetensors:   2%|1         | 41.9MB / 2.61GB            

CommitInfo(commit_url='https://huggingface.co/schmuelling/Ministral-3-3B-Instruct-2512-finetome/commit/c3248d3ce83f3d8badad13d39241a16e22372156', commit_message='Upload folder using huggingface_hub', commit_description='', oid='c3248d3ce83f3d8badad13d39241a16e22372156', pr_url=None, repo_url=RepoUrl('https://huggingface.co/schmuelling/Ministral-3-3B-Instruct-2512-finetome', endpoint='https://huggingface.co', repo_type='model', repo_id='schmuelling/Ministral-3-3B-Instruct-2512-finetome'), pr_revision=None, pr_num=None)